In [1]:
import pandas as pd
import geemap
import geemap.foliumap as geemap
import folium
import ee
from folium.plugins import TimestampedGeoJson
# ee.Authenticate() 
ee.Initialize()

C:\Users\hp\miniconda3\envs\lucacode\lib\site-packages\pandas\core\computation\expressions.py:21: UserWarning: Pandas requires version '2.8.4' or newer of 'numexpr' (version '2.7.3' currently installed).
  from pandas.core.computation.check import NUMEXPR_INSTALLED


#### New

In [31]:
df_namunyak =pd.read_csv("42557_Namunyak.csv")
df_namunyak.columns

Index(['Unnamed: 0', 'id', 'extra__id', 'extra__location',
       'extra__recorded_at', 'extra__created_at', 'extra__exclusion_flags',
       'extra__das_tenant_id', 'extra__source', 'extra__subject_id',
       'geometry', 'extra__subject__content_type', 'extra__subject__id',
       'extra__subject__name', 'extra__subject__subject_type',
       'extra__subject__subject_subtype', 'extra__subject__common_name',
       'extra__subject__additional', 'extra__subject__created_at',
       'extra__subject__updated_at', 'extra__subject__is_active',
       'extra__subject__user', 'extra__subject__region',
       'extra__subject__country', 'extra__subject__sex',
       'extra__subject__tracks_available', 'extra__subject__image_url',
       'extra__subject__last_position_status',
       'extra__subject__last_position_date', 'extra__subject__last_position',
       'extra__subject__device_status_properties', 'extra__subject__url',
       'extra__subject__hex', 'groupby_col', 'fixtime', 'junk_status'

In [7]:

# Load the CSV file
df = pd.read_csv('42557_Namunyak.csv')

# Ensure the 'fixtime' column is converted to a datetime object with UTC timezone
df['timestamp'] = pd.to_datetime(df['fixtime']).dt.tz_convert('UTC')

# Define start and end dates in UTC
start_date = pd.to_datetime('2024-02-23').tz_localize('UTC')
end_date = pd.to_datetime('2024-12-28').tz_localize('UTC')

# Filter data between the specified dates
df_filtered = df[(df['timestamp'] >= start_date) & (df['timestamp'] <= end_date)]

# Check if there are any entries in the filtered dataframe
if df_filtered.empty:
    raise ValueError("No data found for the specified date range.")

# Initialize folium map at the first location
initial_location = [df_filtered.iloc[0]['latitude'], df_filtered.iloc[0]['longitude']]
figure = folium.Figure() 
m = geemap.Map(location=initial_location, zoom_start=10)
# m.add_to(figure)
# HTML template for the title
title_html = '''
     <div style="
     position: relative; 
     top: 0px; left: 50%; transform: translateX(-50%); width: 100%; text-align: center; font-size:24px; 
     background-color: white; padding: 0px; border: 2px solid grey; z-index:9999; height:0px;
     ">
     <b>Animated Track Movement of collared Lion-Namunyak</b>
     </div>
     '''

# Add the legend and title to the map
m.get_root().html.add_child(folium.Element(title_html))
# Create the features list to include line segments with time
features = []

# Generate line segments from the filtered data
for i in range(len(df_filtered) - 1):
    start_row = df_filtered.iloc[i]
    end_row = df_filtered.iloc[i + 1]
    
    line_feature = {
        "type": "Feature",
        "geometry": {
            "type": "LineString",
            "coordinates": [
                [start_row['longitude'], start_row['latitude']],
                [end_row['longitude'], end_row['latitude']]
            ],
        },
        "properties": {
            "times": [
                start_row['timestamp'].strftime('%Y-%m-%dT%H:%M:%S'),
                end_row['timestamp'].strftime('%Y-%m-%dT%H:%M:%S')
            ],
            "style": {
                "color": "blue",  # Customize the color
                "weight": 2,
            },
        },
    }
    
    features.append(line_feature)

# Create the TimestampedGeoJson layer
timestamped_geojson = TimestampedGeoJson({
    "type": "FeatureCollection",
    "features": features,
}, period="PT1H",  # Adjust period based on your data frequency
   add_last_point=False,  # Do not add the last point to the map
   auto_play=False,  # Auto-play the animation
   loop=False,  # Disable looping the animation
   max_speed=100,  # Animation speed
   loop_button=True,  # Add loop button
   date_options='YYYY-MM-DD HH:mm:ss',  # Format for the time slider
   time_slider_drag_update=True)  # Allow dragging the slider to update the map

# Add the time slider to the map
timestamped_geojson.add_to(m)

# Add geofence layers
MaraROI = ee.FeatureCollection("projects/ee-mosongjnvscode/assets/MasaiMaraTrueROI")
m.addLayer(MaraROI,{},"MaraROI")
color="red"
maracattle=ee.FeatureCollection("projects/ee-mosongjnvscode/assets/Naboisho_Cattles")
m.addLayer(maracattle, {
                "color": "red",  # Customize the color
                
            },
"maracattle")

m.setCenter(lon=35.33028428992364, lat=-1.403374983472325, zoom=10)
legend_dict = {
    'Mara-Study Area': '000000',
    'Namunyak Tracking': '0000FF',
    'Mara Tagged Cattle':'FF0000',
}

m.add_legend(title="Legend", legend_dict=legend_dict)

# Display map
m.save("Namunyak.html")


m

In [3]:
###Cattles + Lion

In [6]:

# Load the CSV file
df = pd.read_csv('Naboisho_Cattles.csv')
lion_df = pd.read_csv('42557_Namunyak.csv')


# Ensure the 'fixtime' column is converted to a datetime object with UTC timezone
df['timestamp'] = pd.to_datetime(df['fixtime']).dt.tz_convert('UTC')
lion_df['timestamp'] = pd.to_datetime(lion_df['fixtime']).dt.tz_convert('UTC')


# Define start and end dates in UTC
start_date = pd.to_datetime('2024-02-23').tz_localize('UTC')
end_date = pd.to_datetime('2024-12-28').tz_localize('UTC')

# Filter data between the specified dates
df_filtered = df[(df['timestamp'] >= start_date) & (df['timestamp'] <= end_date)]
df_filtered_Lion = lion_df[(lion_df['timestamp'] >= start_date) & (lion_df['timestamp'] <= end_date)]



# Initialize folium map at the first location
initial_location = [df_filtered.iloc[0]['latitude'], df_filtered.iloc[0]['longitude']]
initial_location_lion = [df_filtered_Lion.iloc[0]['latitude'], df_filtered_Lion.iloc[0]['longitude']]



figure = folium.Figure() 
m = geemap.Map(location=initial_location, zoom_start=10)
# m.add_to(figure)
# HTML template for the title
title_html = '''
     <div style="
     position: relative; 
     top: 0px; left: 50%; transform: translateX(-50%); width: 100%; text-align: center; font-size:24px; 
     background-color: white; padding: 0px; border: 2px solid grey; z-index:9999; height:0px;
     ">
     <b>Animated Track Movement of collared Lion-Namunyak</b>
     </div>
     '''

# Add the legend and title to the map
m.get_root().html.add_child(folium.Element(title_html))
# Create the features list to include line segments with time
features = []

# Generate line segments from the filtered data
for i in range(len(df_filtered) - 1):
    start_row = df_filtered.iloc[i]
    end_row = df_filtered.iloc[i + 1]
    
    line_feature = {
        "type": "Feature",
        "geometry": {
            "type": "LineString",
            "coordinates": [
                [start_row['longitude'], start_row['latitude']],
                [end_row['longitude'], end_row['latitude']]
            ],
        },
        "properties": {
            "times": [
                start_row['timestamp'].strftime('%Y-%m-%dT%H:%M:%S'),
                end_row['timestamp'].strftime('%Y-%m-%dT%H:%M:%S')
            ],
            "style": {
                "color": "blue",  # Customize the color
                "weight": 2,
            },
        },
    }
    
    features.append(line_feature)

# Create the TimestampedGeoJson layer
timestamped_geojson = TimestampedGeoJson({
    "type": "FeatureCollection",
    "features": features,
}, period="PT1H",  # Adjust period based on your data frequency
   add_last_point=False,  # Do not add the last point to the map
   auto_play=False,  # Auto-play the animation
   loop=False,  # Disable looping the animation
   max_speed=100,  # Animation speed
   loop_button=True,  # Add loop button
   date_options='YYYY-MM-DD HH:mm:ss',  # Format for the time slider
   time_slider_drag_update=True)  # Allow dragging the slider to update the map

# Add the time slider to the map
timestamped_geojson.add_to(m)

# Add geofence layers
MaraROI = ee.FeatureCollection("projects/ee-mosongjnvscode/assets/MasaiMaraTrueROI")
m.addLayer(MaraROI,{},"MaraROI")
color="red"
maracattle=ee.FeatureCollection("projects/ee-mosongjnvscode/assets/Naboisho_Cattles")
m.addLayer(maracattle, {
                "color": "red",  # Customize the color
                
            },
"maracattle")

m.setCenter(lon=35.33028428992364, lat=-1.403374983472325, zoom=10)
legend_dict = {
    'Mara-Study Area': '000000',
    'Namunyak Tracking': '0000FF',
    'Mara Tagged Cattle':'FF0000',
}

m.add_legend(title="Legend", legend_dict=legend_dict)

# Display map
m.save("Namunyak.html")


m

FileNotFoundError: [Errno 2] No such file or directory: 'Naboisho_Cattles.csv'

#### Kayioni-Cheetah

In [48]:

# Load the CSV file
df = pd.read_csv('KayioniV2.csv')

# Ensure the 'fixtime' column is converted to a datetime object with UTCa timezone
df['timestamp'] = pd.to_datetime(df['fixtime']).dt.tz_convert('UTC')

# Define start and end dates in UTC
start_date = pd.to_datetime('2024-09-12').tz_localize('UTC')
end_date = pd.to_datetime('2024-10-12').tz_localize('UTC')

# Filter data between the specified dates
df_filtered = df[(df['timestamp'] >= start_date) & (df['timestamp'] <= end_date)]

# Check if there are any entries in the filtered dataframe
if df_filtered.empty:
    raise ValueError("No data found for the specified date range.")

# Initialize folium map at the first location
initial_location = [df_filtered.iloc[0]['latitude'], df_filtered.iloc[0]['longitude']]
figure = folium.Figure() 
m = geemap.Map(location=initial_location, zoom_start=10)
# m.add_to(figure)
# HTML template for the title
title_html = '''
     <div style="
     position: relative; 
     top: 0px; left: 50%; transform: translateX(-50%); width: 100%; text-align: center; font-size:24px; 
     background-color: white; padding: 0px; border: 2px solid grey; z-index:9999; height:0px;
     ">
     <b>Animated Track Movement of collared Cheetah-Kayioni</b>
     </div>
     '''

# Add the legend and title to the map
m.get_root().html.add_child(folium.Element(title_html))
# Create the features list to include line segments with time
features = []

# Generate line segments from the filtered data
for i in range(len(df_filtered) - 1):
    start_row = df_filtered.iloc[i]
    end_row = df_filtered.iloc[i + 1]
    
    line_feature = {
        "type": "Feature",
        "geometry": {
            "type": "LineString",
            "coordinates": [
                [start_row['longitude'], start_row['latitude']],
                [end_row['longitude'], end_row['latitude']]
            ],
        },
        "properties": {
            "times": [
                start_row['timestamp'].strftime('%Y-%m-%dT%H:%M:%S'),
                end_row['timestamp'].strftime('%Y-%m-%dT%H:%M:%S')
            ],
            "style": {
                "color": "blue",  # Customize the color
                "weight": 2,
            },
        },
    }
    
    features.append(line_feature)

# Create the TimestampedGeoJson layer
timestamped_geojson = TimestampedGeoJson({
    "type": "FeatureCollection",
    "features": features,
}, period="PT1H",  # Adjust period based on your data frequency
   add_last_point=False,  # Do not add the last point to the map
   auto_play=False,  # Auto-play the animation
   loop=False,  # Disable looping the animation
   max_speed=100,  # Animation speed
   loop_button=True,  # Add loop button
   date_options='YYYY-MM-DD HH:mm:ss',  # Format for the time slider
   time_slider_drag_update=True)  # Allow dragging the slider to update the map

# Add the time slider to the map
timestamped_geojson.add_to(m)

# Add geofence layers
MaraROI = ee.FeatureCollection("projects/ee-mosongjnvscode/assets/MasaiMaraTrueROI")
m.addLayer(MaraROI,{},"MaraROI")
color="red"
maracattle=ee.FeatureCollection("projects/ee-mosongjnvscode/assets/Siana_RipoiTagged")
m.addLayer(maracattle, {
                "color": "red",  # Customize the color
                
            },
"maracattle")

m.setCenter(lon=35.33028428992364, lat=-1.403374983472325, zoom=10)
legend_dict = {
    'Mara-Study Area': '000000',
    'Kayioni Tracks': '0000FF',
    'Mara Tagged Cattle':'FF0000',
}

m.add_legend(title="Legend", legend_dict=legend_dict)

# Display map
m.save("Kayionmi.html")


m

In [20]:
dfs = [pd.read_csv('KayioniV2.csv'), pd.read_csv('D:\@Starks-Industries\Mara Predator Conservation Programme(MPCP)\KWS\Maraedits/2205B0011.csv')]  # Add more datasets as needed


In [37]:
# List of DataFrames to handle multiple datasets
dfs = [pd.read_csv('2205B0113.csv'), pd.read_csv('2205B0011.csv'),
       pd.read_csv('2205B0123.csv'),pd.read_csv('2205B0317.csv'),
      pd.read_csv('2205B0327.csv'),pd.read_csv('2205B0388.csv'),
      pd.read_csv('2205B1423.csv'),pd.read_csv('2207B1531.csv'),
       pd.read_csv('2207B1801.csv'),pd.read_csv('2207B1831.csv')]  # Add more datasets as needed

# Ensure the 'fixtime' column is converted to a datetime object with UTC timezone for all DataFrames
for i, df in enumerate(dfs):
    df['timestamp'] = pd.to_datetime(df['fixtime']).dt.tz_convert('UTC')
    dfs[i] = df

# Define start and end dates in UTC
start_date = pd.to_datetime('2024-07-01').tz_localize('UTC')
end_date = pd.to_datetime('2024-10-19').tz_localize('UTC')

# Initialize an empty list to hold the filtered data from all DataFrames
filtered_dfs = []

# Filter data between the specified dates for each DataFrame
for df in dfs:
    df_filtered = df[(df['timestamp'] >= start_date) & (df['timestamp'] <= end_date)]
    
    # Check if there are any entries in the filtered dataframe
    if df_filtered.empty:
        raise ValueError(f"No data found for the specified date range in one of the datasets.")
    
    filtered_dfs.append(df_filtered)

# Initialize folium map at the first location of the first dataset
initial_location = [filtered_dfs[0].iloc[0]['latitude'], filtered_dfs[0].iloc[0]['longitude']]
figure = folium.Figure()
m = geemap.Map(location=initial_location, zoom_start=10)

# HTML template for the title
title_html = '''
     <div style="
     position: relative; 
     top: 0px; left: 50%; transform: translateX(-50%); width: 100%; text-align: center; font-size:24px; 
     background-color: white; padding: 0px; border: 2px solid grey; z-index:9999; height:0px;
     ">
     <b>Animated Track Movement of Collared Lion & Tagged Cattle</b>
     </div>
     '''

# Add the title to the map
m.get_root().html.add_child(folium.Element(title_html))

# Create the features list to include line segments from all DataFrames
features = []

# Generate line segments for each filtered DataFrame
for df_filtered in filtered_dfs:
    for i in range(len(df_filtered) - 1):
        start_row = df_filtered.iloc[i]
        end_row = df_filtered.iloc[i + 1]

        line_feature = {
            "type": "Feature",
            "geometry": {
                "type": "LineString",
                "coordinates": [
                    [start_row['longitude'], start_row['latitude']],
                    [end_row['longitude'], end_row['latitude']]
                ],
            },
            "properties": {
                "times": [
                    start_row['timestamp'].strftime('%Y-%m-%dT%H:%M:%S'),
                    end_row['timestamp'].strftime('%Y-%m-%dT%H:%M:%S')
                ],
                "style": {
                    "color": "blue",  # Customize the color for each dataset if needed
                    "weight": 2,
                },
            },
        }

        features.append(line_feature)

# Create the TimestampedGeoJson layer
timestamped_geojson = TimestampedGeoJson({
    "type": "FeatureCollection",
    "features": features,
}, period="PT1H",  # Adjust period based on your data frequency
   add_last_point=False,  # Do not add the last point to the map
   auto_play=False,  # Auto-play the animation
   loop=False,  # Disable looping the animation
   max_speed=100,  # Animation speed
   loop_button=True,  # Add loop button
   date_options='YYYY-MM-DD HH:mm:ss',  # Format for the time slider
   time_slider_drag_update=True)  # Allow dragging the slider to update the map

# Add the time slider to the map
timestamped_geojson.add_to(m)

# Add geofence layers
MaraROI = ee.FeatureCollection("projects/ee-mosongjnvscode/assets/MasaiMaraTrueROI")
m.addLayer(MaraROI, {}, "MaraROI")

maracattle = ee.FeatureCollection("projects/ee-mosongjnvscode/assets/Siana_RipoiTagged")
m.addLayer(maracattle, {
                "color": "red",  # Customize the color for tagged cattle
            }, "maracattle")

m.setCenter(lon=35.33028428992364, lat=-1.403374983472325, zoom=10)

# Legend for the map
legend_dict = {
    'Mara-Study Area': '000000',
    'Mara Cattle Tracks': '0000FF',
    'Collared Lion': 'FF0000',
}

m.add_legend(title="Legend", legend_dict=legend_dict)

# Save map to HTML file
m.save("MultiDatasetTracks.html")
m

In [54]:
# List of DataFrames to handle multiple datasets
dfs = [pd.read_csv('2205B0113.csv'), pd.read_csv('2205B0011.csv'),
       pd.read_csv('2205B0123.csv'),pd.read_csv('2205B0317.csv'),
      pd.read_csv('2205B0327.csv'),pd.read_csv('2205B0388.csv'),
      pd.read_csv('2205B1423.csv'),pd.read_csv('2207B1531.csv'),
       pd.read_csv('2207B1801.csv'),pd.read_csv('2207B1831.csv')]  # Add more datasets as needed
df_lion=pd.read_csv("42557_Namunyak.csv")
# Define start and end dates in UTC
start_date = pd.to_datetime('2024-02-23').tz_localize('UTC')
end_date = pd.to_datetime('2024-12-28').tz_localize('UTC')
df_lion['timestamp'] = pd.to_datetime(df_lion['fixtime']).dt.tz_convert('UTC')

df_filtered_subject = df_lion[(df_lion['timestamp'] >= start_date) & (df_lion['timestamp'] <= end_date)]

# Ensure the 'fixtime' column is converted to a datetime object with UTC timezone for all DataFrames
for i, df in enumerate(dfs):
    df['timestamp'] = pd.to_datetime(df['fixtime']).dt.tz_convert('UTC')
    dfs[i] = df

# Define start and end dates in UTC
# Define start and end dates in UTC
start_date = pd.to_datetime('2024-07-01').tz_localize('UTC')
end_date = pd.to_datetime('2024-10-19').tz_localize('UTC')

# Initialize an empty list to hold the filtered data from all DataFrames
filtered_dfs = []

# Filter data between the specified dates for each DataFrame
for df in dfs:
    df_filtered = df[(df['timestamp'] >= start_date) & (df['timestamp'] <= end_date)]
    
    # Check if there are any entries in the filtered dataframe
    if df_filtered.empty:
        raise ValueError(f"No data found for the specified date range in one of the datasets.")
    
    filtered_dfs.append(df_filtered)

# Initialize folium map at the first location of the first dataset
initial_location = [filtered_dfs[0].iloc[0]['latitude'], filtered_dfs[0].iloc[0]['longitude']]
figure = folium.Figure()
m = geemap.Map(location=initial_location, zoom_start=10)

# HTML template for the title
title_html = '''
     <div style="
     position: relative; 
     top: 0px; left: 50%; transform: translateX(-50%); width: 100%; text-align: center; font-size:30px; 
     background-color: white; padding: 0px; border: 2px solid grey; z-index:9999; height:0px;
     ">
     <b>Animated Track Movement of Collared Lion & Tagged Cattle</b>
     </div>
     '''

# Add the title to the map
m.get_root().html.add_child(folium.Element(title_html))

# Create the features list to include line segments from all DataFrames
features = []
# Generate line segments from the filtered data
for i in range(len(df_filtered_subject) - 1):
    start_row_subject = df_filtered_subject.iloc[i]
    end_row_subject = df_filtered_subject.iloc[i + 1]
    
    line_feature_subject = {
        "type": "Feature",
        "geometry": {
            "type": "LineString",
            "coordinates": [
                [start_row_subject['longitude'], start_row_subject['latitude']],
                [end_row_subject['longitude'], end_row_subject['latitude']]
            ],
        },
        "properties": {
            "times": [
                start_row_subject['timestamp'].strftime('%Y-%m-%dT%H:%M:%S'),
                end_row_subject['timestamp'].strftime('%Y-%m-%dT%H:%M:%S')
            ],
            "style": {
                "color": "red",  # Customize the color
                "weight": 2,
            },
        },
    }
    
    features.append(line_feature_subject)
# Generate line segments for each filtered DataFrame
for df_filtered in filtered_dfs:
    for i in range(len(df_filtered) - 1):
        start_row = df_filtered.iloc[i]
        end_row = df_filtered.iloc[i + 1]

        line_feature = {
            "type": "Feature",
            "geometry": {
                "type": "LineString",
                "coordinates": [
                    [start_row['longitude'], start_row['latitude']],
                    [end_row['longitude'], end_row['latitude']]
                ],
            },
            "properties": {
                "times": [
                    start_row['timestamp'].strftime('%Y-%m-%dT%H:%M:%S'),
                    end_row['timestamp'].strftime('%Y-%m-%dT%H:%M:%S')
                ],
                "style": {
                    "color": "blue",  # Customize the color for each dataset if needed
                    "weight": 2,
                },
            },
        }

        features.append(line_feature)

# Create the TimestampedGeoJson layer
timestamped_geojson = TimestampedGeoJson({
    "type": "FeatureCollection",
    "features": features,
}, period="PT6H",  # Adjust period based on your data frequency
   add_last_point=False,  # Do not add the last point to the map
   auto_play=False,  # Auto-play the animation
   loop=False,  # Disable looping the animation
   max_speed=900,  # Animation speed
   loop_button=True,  # Add loop button
   date_options='YYYY-MM-DD HH:mm:ss',  # Format for the time slider
   time_slider_drag_update=True)  # Allow dragging the slider to update the map

# Add the time slider to the map
timestamped_geojson.add_to(m)

# Add geofence layers
MaraROI = ee.FeatureCollection("projects/ee-mosongjnvscode/assets/MasaiMaraTrueROI")
# m.addLayer(MaraROI, {}, "MaraROI")

# Buildings
buildings=ee.FeatureCollection("GOOGLE/Research/open-buildings/v1/polygons")
m.setCenter(lon=35.33028428992364, lat=-1.403374983472325, zoom=10)
# Buildings
buildings=ee.FeatureCollection("projects/ee-mosongjnvscode/assets/Mara_buildings1")
m.addLayer(buildings, {
                "color": "black",  # Customize the color
                
            },
"Mara Households")
# Legend for the map
legend_dict = {
    'Built-Up Areas': '000000',
    'Mara Cattle Tracks': '0000FF',
    'Collared Lion': 'FF0000',
}

m.add_legend(title="Legend", legend_dict=legend_dict)

# Save map to HTML file
m.save("Lion_VS_Cattles.html")
m

#### Edits

In [46]:

aoi=ee.FeatureCollection("projects/ee-mosongjnvscode/assets/MaraBoundary_habitat")
buildings=ee.FeatureCollection("GOOGLE/Research/open-buildings/v1/polygons")
AOI_BUILDINGS = buildings.filter('confidence >= 0.68 && confidence < 0.80')\
.filterBounds(aoi)
m.addLayer(AOI_BUILDINGS, {color: '00FF00'}, 'Buildings confidence >= 0.70');
m